In [3]:
print("Performing chunk summary : " + "mpt-7B")

from langchain import PromptTemplate
import torch
import transformers
from transformers import AutoTokenizer
from langchain.llms import TextGen
from langchain.prompts import Prompt
from langchain.chains.summarize import load_summarize_chain
from langchain.text_splitter import SpacyTextSplitter

text_splitter = SpacyTextSplitter(
    chunk_size = 5000,
    chunk_overlap  = 200,
    length_function = len
)

with open("transcript.txt") as f:
    txt = f.read()

docs = text_splitter.create_documents([txt])


Performing chunk summary : mpt-7B


/Users/user/.pyenv/versions/3.11.2/lib/python3.11/site-packages/spacy/pipeline/lemmatizer.py:211: UserWarning: [W108] The rule-based lemmatizer did not find POS annotation for one or more tokens. Check that your pipeline includes components that assign token.pos, typically 'tagger'+'attribute_ruler' or 'morphologizer'.
  warnings.warn(Warnings.W108)


In [12]:
from langchain import LLMChain
llm_summary = TextGen(model_url="http://216.153.52.83:5000", max_new_tokens=250)
summary_prompt_template = """Write a concise two line summary of the following:


{text}


CONCISE SUMMARY:

"""
summary_prompt = PromptTemplate(template=summary_prompt_template, input_variables=["text"])
summary_chain = LLMChain(llm=llm_summary, prompt=summary_prompt, verbose=True)

In [13]:
llm_subject = TextGen(model_url="http://216.153.52.83:5000", max_new_tokens=100)
subject_prompt_template = """Summarize the text below in a subject line:


{text}


SUBJECT LINE:

"""
subject_prompt = PromptTemplate(template=subject_prompt_template, input_variables=["text"])
subject_chain = LLMChain(llm=llm_subject, prompt=subject_prompt, verbose=True)

In [15]:
summaries = []
subjects = []
for doc in docs:
    summary = summary_chain.run({"text": doc.page_content})
    summaries.append(summary)
    subject = subject_chain.run({"text": doc.page_content})
    subjects.append(subject)


# for c in chunks:
#     summary = llm.generate(c, max_length=100, num_return_sequences=1)[0]
#     summaries.append(summary)

with open("mpt-7b-summaries.txt", "a") as f:
    for summary, subject in zip(summaries, subjects):
        f.write("SUBJECT: " + subject + "\n")
        f.write("SUMMARY: " + summary + "\n\n")




> Entering new LLMChain chain...
Prompt after formatting:
Write a concise two line summary of the following:


We 're joined next by Thomas Curian , CEO of Google Cloud , and Alexander Wang , CEO and founder of Scale AI .

Thomas joined Google in November 2018 as the CEO of Google Cloud .

Prior to Google , Thomas spent 22 years at Oracle , where most recently he was president of product development .

Before that , Thomas worked at McKinsey as a business analyst and engagement manager .

His nearly 30 years of experience have given him a deep knowledge of engineering enterprise relationships and leadership of large organizations .

Thomas 's degrees include an MBA in administration and management from Stanford University , as an RJ Miller scholar and a BSEE in electrical engineering and computer science from Princeton University , where he graduated suma cum laude .  

Thomas serves as a member of the Stanford graduate School of Business Advisory Council and Princeton University Sch